# Determinate if yacrd is efficient for RNA

Methodology, use Badread to generate 32x long reads on human transcriptome. 

Use minimap2 mapping of this reads against transcriptome to determinate chimera create by Badread. We say a reads his a chimera when his map on two different transcipt.

### Get truth

In [1]:
chimera2refs = dict()

with open("data/human/reads.fasta") as fh:
    for line in fh:
        if line.startswith(">"):
            if "chimera" in line:
                line = line.split(" ")
                reads = line[0][1:]
                refs = frozenset((line[1].split(",")[0], line[3].split(",")[0]))
                chimera2refs[reads] = refs

## Default parameter

### Get yacrd result

In [2]:
import csv

yacrd = set()
all_discard = set()
nb_not_cov = 0

with open("detect/human/chimera.yacrd") as fh:
    reader = csv.reader(fh, delimiter="\t")
    for row in reader:
        if row[0] == "Chimeric":
            yacrd.add(row[1])
            all_discard.add(row[1])
        elif row[0] == "NotCovered":
            all_discard.add(row[1])
            
print(f"Number of chimeric reads {len(yacrd)} discard {len(all_discard)}")

Number of chimeric reads 46496 discard 47364


### Compute result

In [3]:
truth = set(chimera2refs.keys())

tp = len(truth & yacrd)
fp = len(yacrd - truth)
tn = len(truth - yacrd)

precision = tp / (tp + fp)
recall    = tp / len(truth)
print(f"Precision: {precision}")
print(f"Recall   : {recall}")
print(f"F1-score : {2*(precision * recall)/(precision + recall)}")

Precision: 1.0
Recall   : 0.8297967269287742
F1-score : 0.9069824147314419


In [4]:
truth = set(chimera2refs.keys())

tp = len(truth & all_discard)
fp = len(all_discard - truth)
tn = len(truth - all_discard)

precision = tp / (tp + fp)
recall    = tp / len(truth)
print(f"Precision: {precision}")
print(f"Recall   : {recall}")
print(f"F1-score : {2*(precision * recall)/(precision + recall)}")

Precision: 0.9996621906933536
Recall   : 0.845002052362001
F1-score : 0.9158486223004536


## Reference Coverage

In [5]:
from collections import defaultdict

ref2bases = defaultdict(int)

with open("data/human/reads.fasta") as fh:
    for line in fh:
        if line.startswith(">") and "chimera" not in line:
            line = line.split(" ")
            ref_name = line[1].split(",")[0]
            base = int(line[3].split("=")[1])
            ref2bases[ref_name] += base
            
ref2len = dict()
with open("data/human/transcriptome.fasta") as fh:
    ref_name = None
    for line in fh:
        if line.startswith(">"):
            line = line.split(" ")
            ref_name = line[0][1:]
        elif ref_name is not None:
            ref2len[ref_name] = len(line)

In [6]:
ref2cov = dict()
for ref, length in ref2len.items():
    ref2cov[ref] = ref2bases[ref] / length

In [8]:
import altair
import pandas

df = pandas.DataFrame.from_dict(ref2cov, orient="index", columns=["coverage"])

altair.data_transformers.disable_max_rows()

altair.Chart(df).mark_bar().encode(
    altair.X("coverage:Q", bin=altair.Bin(maxbins=60)),
    y='count()',
)


alt.Chart(...)

## Chimera coverage

In [15]:
import altair
import pandas

data = list()

for (reads, refs) in chimera2refs.items():
    if "junk_seq" in refs or "random_seq" in refs:
        continue

    ref1, ref2 = refs
    ref1, ref2 = (ref1, ref2) if ref2cov[ref1] > ref2cov[ref2] else (ref2, ref1)
    data.append((reads, ref2cov[ref1], ref2cov[ref2], reads in yacrd))
 
df = pandas.DataFrame(data, columns=["reads", "coverage 1", "coverage 2", "yacrd"]) 

df = df[df["yacrd"] != True]

altair.Chart(df).mark_point(size=0.1).encode(
    x='coverage 1',
    y='coverage 2',
    color="yacrd"
)

alt.Chart(...)